In [1]:
import mediapipe as mp
from mediapipe.tasks import python
from mediapipe.tasks.python import vision
import cv2
import time
import csv
import queue
from datetime import datetime
import math
import numpy as np

/Users/beni/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [2]:
model_path = "/Users/beni/Desktop/Climbing Technique Tracker/Climbing_Tracker/pose_landmarker_full.task"

In [3]:
"""The code in this block is partly taken from the official MediaPipe documentation and can be found 
here: https://ai.google.dev/edge/mediapipe/solutions/vision/pose_landmarker/python#live-stream_1"""

BaseOptions = mp.tasks.BaseOptions
PoseLandmarker = mp.tasks.vision.PoseLandmarker
PoseLandmarkerOptions = mp.tasks.vision.PoseLandmarkerOptions
PoseLandmarkerResult = mp.tasks.vision.PoseLandmarkerResult
VisionRunningMode = mp.tasks.vision.RunningMode

saved_results = queue.Queue()


def print_result(result: PoseLandmarkerResult, output_image: mp.Image, timestamp_ms: int):
    print('pose landmarker result: {}'.format(result))
    saved_results.put(result)
    saved_results.put(timestamp_ms)


options = PoseLandmarkerOptions(
    base_options=BaseOptions(model_asset_path=model_path),
    running_mode=VisionRunningMode.LIVE_STREAM, #sets the running mode to live stream
    result_callback=print_result)


"""The following code is written by myself using the OpenCV and MediaPipe documentation for help which
can be found in the readme file"""

#check how many frames per second Qsense sensors output
frames_per_second = 10
time_between_frames = 1 / frames_per_second


with PoseLandmarker.create_from_options(options) as landmarker:
    #Use openCV VideoCapture to start capturing from the webcam
    start_time = time.time()

    capture = cv2.VideoCapture(0)

    #Create a loop to read the latest frame from the camera using VideoCaptureRead()
    while capture.isOpened():

        ret, frame = capture.read()
     
        if not ret:
            print("broken")
            break

        #Convert the frame receieved from OpenCV to a MediaPipe Image Object
        mp_image = mp.Image(image_format=mp.ImageFormat.SRGB, data=frame)
      
        #landmarker.detect_async(mp_image, timestamp_ms = int(time.time() * 1000))
        #from datetime import datetime
        landmarker.detect_async(mp_image, int(datetime.now().timestamp() * 1000))


        #color = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        cv2.imshow('frame', frame) #first param is window name
        cv2.waitKey(10)

        """The following frame limiter was taken from the following online answer:
         https://www.quora.com/How-do-I-decrease-the-frames-per-second-in-OpenCV-python"""
        
        elapsed_time = time.time() - start_time 
        time_to_wait = time_between_frames - elapsed_time 
        if time_to_wait > 0: 
            time.sleep(time_to_wait)
    

I0000 00:00:1752419639.413555 10966610 gl_context.cc:369] GL version: 2.1 (2.1 Metal - 83.1), renderer: Apple M2 Max
INFO: Created TensorFlow Lite XNNPACK delegate for CPU.
W0000 00:00:1752419639.496137 10966843 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1752419639.507141 10966849 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.


pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[],

W0000 00:00:1752419642.679151 10966844 landmark_projection_calculator.cc:186] Using NORM_RECT without IMAGE_DIMENSIONS is only supported for the square ROI. Provide IMAGE_DIMENSIONS or use PROJECTION_MATRIX.


pose landmarker result: PoseLandmarkerResult(pose_landmarks=[], pose_world_landmarks=[], segmentation_masks=None)
pose landmarker result: PoseLandmarkerResult(pose_landmarks=[[NormalizedLandmark(x=0.8033007383346558, y=0.0755295529961586, z=-0.32742995023727417, visibility=0.984325647354126, presence=0.46392056345939636), NormalizedLandmark(x=0.8145305514335632, y=0.04400332644581795, z=-0.3048240840435028, visibility=0.9753744006156921, presence=0.28787097334861755), NormalizedLandmark(x=0.8215897083282471, y=0.04406695067882538, z=-0.3049783408641815, visibility=0.9704775214195251, presence=0.2768387198448181), NormalizedLandmark(x=0.8298579454421997, y=0.04308067634701729, z=-0.3052690923213959, visibility=0.9716089963912964, presence=0.25717684626579285), NormalizedLandmark(x=0.7928822040557861, y=0.04752642288804054, z=-0.3027474582195282, visibility=0.9787584543228149, presence=0.41038206219673157), NormalizedLandmark(x=0.7875061631202698, y=0.04961656779050827, z=-0.302821278572

KeyboardInterrupt: 

In [4]:
def calculate_elbow_angle(shoulder_landmark, elbow_landmark, wrist_landmark):

    #convert landmark coordinates into vectors
    #calculate vector without z value to improve accuracy
    vector_s_e = [shoulder_landmark.x - elbow_landmark.x, shoulder_landmark.y - elbow_landmark.y]
    vector_w_e = [wrist_landmark.x - elbow_landmark.x, wrist_landmark.y - elbow_landmark.y]
   
    """dot product of the two vectors: code adapted from 
    https://www.geeksforgeeks.org/python/how-to-calculate-dot-product-of-two-vectors-in-python/""" 
    dot_product = np.dot(vector_s_e, vector_w_e)
    


    """magnitude of the two vectors: code apated from
    https://stackoverflow.com/questions/9171158/how-do-you-get-the-magnitude-of-a-vector-in-numpy"""
    magnitude_vector_s_e = np.linalg.norm(vector_s_e)
    magnitude_vector_w_e = np.linalg.norm(vector_w_e)
    

    """final equation to calculate angle"""
    angle = math.degrees(math.acos(dot_product / ((magnitude_vector_s_e) * (magnitude_vector_w_e))))
    
    return angle

In [5]:
def midpoint_two_points(landmark_one, landmark_two):
    return [(landmark_one.x + landmark_two.x)/2, 
            (landmark_one.y + landmark_two.x)/2]

In [6]:
def midpoint_four_points(landmark_one, landmark_two, landmark_three, landmark_four):
    centre_1 = [(landmark_one.x + landmark_two.x)/2, (landmark_one.y + landmark_two.x)/2]
    centre_2 = [(centre_1[0] + landmark_three.x)/2, (centre_1[1] + landmark_three.y)/2]
    centre_3 = [(centre_2[0] + landmark_four.x)/2, (centre_2[1] + landmark_four.y)/2]

    return centre_3

In [7]:
def calculate_centre_of_mass(landmark):
    #should I use local or world coordinates? 

    #check if using nose is correct for centre of head
    head_centre = [landmark.pose_landmarks[0][0].x, landmark.pose_landmarks[0][0].y]
    
    left_upper_arm_centre = midpoint_two_points(landmark.pose_landmarks[0][11], landmark.pose_landmarks[0][13])
    right_upper_arm_centre = midpoint_two_points(landmark.pose_landmarks[0][12], landmark.pose_landmarks[0][14])
    
    left_lower_arm_centre = midpoint_two_points(landmark.pose_landmarks[0][13], landmark.pose_landmarks[0][15])                
    right_lower_arm_centre = midpoint_two_points(landmark.pose_landmarks[0][14], landmark.pose_landmarks[0][16])

    left_hand_centre = midpoint_four_points(landmark.pose_landmarks[0][15], landmark.pose_landmarks[0][21], landmark.pose_landmarks[0][19], landmark.pose_landmarks[0][17])
    right_hand_centre = midpoint_four_points(landmark.pose_landmarks[0][16], landmark.pose_landmarks[0][22], landmark.pose_landmarks[0][20], landmark.pose_landmarks[0][18])

    torso_centre = midpoint_four_points(landmark.pose_landmarks[0][12], landmark.pose_landmarks[0][11], landmark.pose_landmarks[0][24], landmark.pose_landmarks[0][23])

    pelvis_centre = midpoint_two_points(landmark.pose_landmarks[0][24], landmark.pose_landmarks[0][23])

    left_upper_thigh_centre = midpoint_two_points(landmark.pose_landmarks[0][23], landmark.pose_landmarks[0][25])
    right_upper_thigh_centre = midpoint_two_points(landmark.pose_landmarks[0][24], landmark.pose_landmarks[0][26])

    left_lower_thigh_centre = midpoint_two_points(landmark.pose_landmarks[0][25], landmark.pose_landmarks[0][27])
    right_lower_thigh_centre = midpoint_two_points(landmark.pose_landmarks[0][26], landmark.pose_landmarks[0][28])

    return [1,1]


In [ ]:
#adding column headers to the array
results = [
    ['time stamp', 'landmark #1', 'landmark #2', 'landmark #3', 'landmark #4', 'landmark #5',
    'landmark #6', 'landmark #7', 'landmark #8', 'landmark #9', 'landmark #10', 'landmark #11',
    'landmark #12', 'landmark #13', 'landmark #14', 'landmark #15', 'landmark #16', 'landmark #17',
    'landmark #18', 'landmark #19', 'landmark #20', 'landmark #21', 'landmark #22', 'landmark #23',
    'landmark #24', 'landmark #25', 'landmark #26', 'landmark #27', 'landmark #28', 'landmark #29',
    'landmark #30','landmark #31','landmark #32', 'elbow angle', 'Centre of mass']
]

while not saved_results.empty():
    
    landmark = saved_results.get() #get pose_landmark for each frame
    try:
        landmarks = [] #initialize an array for each indidual landmark in a frame (33 total)
        for i in range(0,32):
            landmark_point = landmark.pose_landmarks[0][i] #get each landmark (0, 32) for the 0th person in the frame
            landmarks.append(landmark_point)
    except:
        print("no landmarks detected") #first couple frames might not detect a person yet

    #calculate elbow angle
    try:
        elbow_ang = calculate_elbow_angle(landmark.pose_landmarks[0][12], landmark.pose_landmarks[0][14], landmark.pose_landmarks[0][16])
    except:
        pass

    try:
        CoM = calculate_centre_of_mass(landmark)
    except:
        pass

    from datetime import datetime, timedelta
    time_stamp = saved_results.get() #get timestamp (comes after each landmark in the queue)
    utc_tz = datetime.utcfromtimestamp(time_stamp / 1000) #convert to readable date time format
    utc_plus_8_tz = utc_tz + timedelta(hours=8) #adjust time zone from UTC to UTC + 8
    
    try:
        results.append([utc_plus_8_tz]+ landmarks + [elbow_ang] + [CoM]) #append landmarks + timestamp into results array
    except:
         results.append([utc_plus_8_tz]+ landmarks) #if no elbow_ang then only add timezone and landmarks


"""CSV code adapted from the following website: https://www.geeksforgeeks.org/python/writing-csv-files-in-python/"""

#each frame is writen into the CSV, each column are the coordinates for a single landmark
with open('results.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerows(results)

no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmarks detected
no landmar